In [2]:
# Custom libraries
from datascienceutils import plotter
from datascienceutils import analyze
from datascienceutils import predictiveModels as pm

# Standard libraries
import json
%matplotlib inline
import datetime
import numpy as np
import pandas as pd
import random

from sklearn import cross_validation
from sklearn import metrics

from bokeh.plotting import figure, show, output_file, output_notebook, ColumnDataSource
from bokeh.charts import Histogram
import bokeh
output_notebook(bokeh.resources.INLINE)

from sqlalchemy import create_engine

/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/sklearn/cross_validation.py:44: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


Loading BokehJS ...

In [3]:
twoSigmaDf = None
with pd.HDFStore("../data/train.h5", "r") as train:
    # Note that the "train" dataframe is the only dataframe in the file
    twoSigmaDf = train.get("train")

In [3]:
twoSigmaDf.describe()

/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/numpy/lib/function_base.py:3834: RuntimeWarning: Invalid value encountered in percentile
  RuntimeWarning)


id     timestamp     derived_0     derived_1     derived_2  \
count  1.710756e+06  1.710756e+06  1.637797e+06  1.629727e+06  1.312105e+06   
mean   1.093858e+03  9.456257e+02 -4.537569e+00  7.729437e+11 -3.321289e-01   
std    6.308563e+02  5.195685e+02  2.497790e+02  7.620848e+13  6.521051e+01   
min    0.000000e+00  0.000000e+00 -2.017497e+04 -7.375435e-02 -9.848880e+03   
25%    5.500000e+02  5.040000e+02           NaN           NaN           NaN   
50%    1.098000e+03  9.560000e+02           NaN           NaN           NaN   
75%    1.657000e+03  1.401000e+03           NaN           NaN           NaN   
max    2.158000e+03  1.812000e+03  3.252527e+03  1.068448e+16  3.823001e+03   

          derived_3     derived_4  fundamental_0  fundamental_1  \
count  1.561285e+06  1.304298e+06   1.686809e+06   1.031686e+06   
mean  -5.047151e-01  1.803233e+01  -2.041142e-02  -5.703752e+08   
std    1.020845e+02  9.260062e+02   2.496619e-01   7.502489e+10   
min   -3.434176e+04 -8.551914e+03  -2.344957e+00  -1.043737e+13   
25%             NaN           NaN            NaN            NaN   
50%             NaN           NaN            NaN            NaN   
75%             NaN           NaN            NaN            NaN   
max    1.239737e+03  6.785965e+04   1.378195e+00   5.203165e+02   

       fundamental_2      ...       technical_36  technical_37  technical_38  \
count   1.341916e+06      ...       1.708204e+06  1.691591e+06  1.691591e+06   
mean   -1.623607e-01      ...      -8.584284e-02 -9.108464e-02 -8.161018e-02   
std     3.675968e+00      ...       6.129349e-01  2.476959e-01  2.333819e-01   
min    -1.077101e+03      ...      -1.687572e+00 -1.000000e+00 -1.000000e+00   
25%              NaN      ...                NaN           NaN           NaN   
50%              NaN      ...                NaN           NaN           NaN   
75%              NaN      ...                NaN           NaN           NaN   
max     7.677125e+01      ...       4.957758e+01  0.000000e+00  0.000000e+00   

       technical_39  technical_40  technical_41  technical_42  technical_43  \
count  1.690740e+06  1.708520e+06  1.666567e+06  1.690755e+06  1.706070e+06   
mean  -7.290059e-02  4.907529e-02  5.236320e-03 -1.700147e-02 -9.735643e-01   
std    2.230485e-01  3.105295e-01  1.134394e-01  2.121332e-01  9.626583e-01   
min   -1.000000e+00 -5.250904e-01 -4.449529e-01 -1.000000e+00 -2.000000e+00   
25%             NaN           NaN           NaN           NaN           NaN   
50%             NaN           NaN           NaN           NaN           NaN   
75%             NaN           NaN           NaN           NaN           NaN   
max    0.000000e+00  1.569265e+00  6.844833e-01  1.000000e+00  0.000000e+00   

       technical_44             y  
count  1.473977e+06  1.710756e+06  
mean   3.881556e-04  2.217474e-04  
std    3.013458e-02  2.242171e-02  
min   -1.265686e-01 -8.609413e-02  
25%             NaN -9.561389e-03  
50%             NaN -1.570681e-04  
75%             NaN  9.520990e-03  
max    1.435858e-01  9.349781e-02  

[8 rows x 111 columns]

In [4]:
twoSigmaDf.columns

Index(['id', 'timestamp', 'derived_0', 'derived_1', 'derived_2', 'derived_3',
       'derived_4', 'fundamental_0', 'fundamental_1', 'fundamental_2',
       ...
       'technical_36', 'technical_37', 'technical_38', 'technical_39',
       'technical_40', 'technical_41', 'technical_42', 'technical_43',
       'technical_44', 'y'],
      dtype='object', length=111)

In [5]:
twoSigmaDf[twoSigmaDf.id==10]['y'].describe()


count    116.000000
mean      -0.000721
std        0.027715
min       -0.086094
25%       -0.011228
50%       -0.002115
75%        0.009515
max        0.093498
Name: y, dtype: float64

In [6]:
grouped_ids = twoSigmaDf.groupby('id').count()

id
0       1646
6        728
7       1543
10       116
11      1813
12      1813
13      1543
14       218
15      1340
16      1745
17       779
18       218
19       829
20      1646
22      1442
23       218
24       932
25      1813
26      1813
27       159
30       932
31      1813
32       218
33       422
38      1813
39      1813
40      1813
41      1813
43      1813
44      1813
        ... 
2115     363
2117     728
2118     829
2120    1745
2121     422
2124     627
2125    1128
2126    1813
2129    1813
2130    1745
2131    1813
2134    1203
2135     960
2136    1290
2137    1646
2138    1813
2139     880
2140    1442
2142    1813
2145    1646
2146    1813
2148    1813
2149    1813
2150    1646
2151    1745
2152     167
2154    1813
2155    1657
2156    1813
2158     150
Name: timestamp, dtype: int64


In [7]:
twoSigmaDf[twoSigmaDf.id==12]['y'].describe()

count    1813.000000
mean        0.000235
std         0.013453
min        -0.070060
25%        -0.006805
50%        -0.000127
75%         0.007031
max         0.093498
Name: y, dtype: float64

In [8]:
twoSigmaDf['timestamp'].nunique()

1813

In [9]:
twoSigmaDf.head()

id  timestamp  derived_0  derived_1  derived_2  derived_3  derived_4  \
0  10          0   0.370326  -0.006316   0.222831  -0.213030   0.729277   
1  11          0   0.014765  -0.038064  -0.017425   0.320652  -0.034134   
2  12          0  -0.010622  -0.050577   3.379575  -0.157525  -0.068550   
3  25          0        NaN        NaN        NaN        NaN        NaN   
4  26          0   0.176693  -0.025284  -0.057680   0.015100   0.180894   

   fundamental_0  fundamental_1  fundamental_2    ...     technical_36  \
0      -0.335633       0.113292       1.621238    ...         0.775208   
1       0.004413       0.114285      -0.210185    ...         0.025590   
2      -0.155937       1.219439      -0.764516    ...         0.151881   
3       0.178495            NaN      -0.007262    ...         1.035936   
4       0.139445      -0.125687      -0.018707    ...         0.630232   

   technical_37  technical_38  technical_39  technical_40  technical_41  \
0           NaN           NaN           NaN     -0.414776           NaN   
1           NaN           NaN           NaN     -0.273607           NaN   
2           NaN           NaN           NaN     -0.175710           NaN   
3           NaN           NaN           NaN     -0.211506           NaN   
4           NaN           NaN           NaN     -0.001957           NaN   

   technical_42  technical_43  technical_44         y  
0           NaN          -2.0           NaN -0.011753  
1           NaN          -2.0           NaN -0.001240  
2           NaN          -2.0           NaN -0.020940  
3           NaN          -2.0           NaN -0.015959  
4           NaN           0.0           NaN -0.007338  

[5 rows x 111 columns]

In [10]:
twoSigmaDf.corr()

id  timestamp  derived_0  derived_1  derived_2  \
id              1.000000   0.003723   0.026267   0.006481  -0.003113   
timestamp       0.003723   1.000000   0.021064   0.006743   0.004869   
derived_0       0.026267   0.021064   1.000000   0.000163   0.000214   
derived_1       0.006481   0.006743   0.000163   1.000000   0.000062   
derived_2      -0.003113   0.004869   0.000214   0.000062   1.000000   
derived_3      -0.005971   0.004510  -0.000075   0.000033  -0.000029   
derived_4      -0.028646  -0.022599  -0.962172  -0.000199  -0.000143   
fundamental_0  -0.034317  -0.057031   0.013534  -0.009425  -0.001155   
fundamental_1  -0.010725   0.006340   0.000293   0.000058  -0.000192   
fundamental_2   0.016523   0.030643   0.010259   0.000039   0.000451   
fundamental_3  -0.069999   0.045453  -0.002664  -0.004988   0.005386   
fundamental_5   0.007988   0.012389  -0.000076  -0.000425   0.000262   
fundamental_6   0.011878   0.046604   0.000274   0.000900   0.000915   
fundamental_7  -0.010475  -0.016935   0.000127  -0.000106   0.001324   
fundamental_8   0.003942   0.074260   0.002773  -0.002110   0.000540   
fundamental_9   0.005791  -0.008665  -0.030520   0.001501   0.012243   
fundamental_10 -0.005151   0.031232  -0.000038  -0.000251   0.000680   
fundamental_11  0.010416   0.039731   0.018678   0.000207   0.000438   
fundamental_12 -0.006450   0.020481   0.000274  -0.000250   0.000293   
fundamental_13  0.001114   0.005355  -0.000670  -0.001720  -0.000072   
fundamental_14  0.002992   0.000588   0.000813  -0.000104  -0.000021   
fundamental_15  0.005301   0.030013  -0.002576  -0.000499   0.000927   
fundamental_16 -0.005930  -0.007450   0.001258   0.000420   0.000131   
fundamental_17 -0.011106  -0.014200   0.000162  -0.000092   0.000075   
fundamental_18 -0.013058  -0.035988   0.005687  -0.000132   0.000124   
fundamental_19  0.010710  -0.003006  -0.000278  -0.000315   0.001554   
fundamental_20  0.008403   0.016208  -0.000071   0.000055  -0.000080   
fundamental_21 -0.012002  -0.151022  -0.013037   0.000217  -0.000483   
fundamental_22  0.010780   0.001684   0.002889  -0.000745   0.000908   
fundamental_23 -0.028041  -0.022023  -0.000203  -0.000250   0.000034   
...                  ...        ...        ...        ...        ...   
technical_13   -0.003230  -0.003866   0.002643  -0.000900   0.000584   
technical_14    0.017147  -0.081467   0.011232  -0.006617  -0.003095   
technical_16    0.001467   0.037699   0.003088  -0.005585   0.000794   
technical_17    0.007084   0.000731   0.006905   0.005382  -0.004998   
technical_18   -0.019438   0.035636  -0.003625   0.002161   0.001203   
technical_19    0.001890  -0.000098  -0.002150   0.005954   0.003601   
technical_20    0.008885   0.026341  -0.012345   0.002952   0.004819   
technical_21    0.006164   0.004171   0.004303   0.001943   0.000493   
technical_22    0.008196   0.002523  -0.024159   0.004630  -0.002631   
technical_24   -0.002025  -0.001062   0.000079  -0.002374  -0.017071   
technical_25   -0.005349   0.000354   0.000876   0.000625   0.004787   
technical_27    0.014553  -0.011583  -0.004679   0.001293  -0.009783   
technical_28   -0.005568   0.001087   0.012108  -0.007819   0.006099   
technical_29    0.028907  -0.174010   0.018467  -0.000894  -0.004022   
technical_30    0.000367   0.015487  -0.009293  -0.002397  -0.001485   
technical_31    0.001253  -0.006459  -0.009835  -0.001314   0.001122   
technical_32   -0.022809   0.003101  -0.000879  -0.007154  -0.001553   
technical_33   -0.006590   0.003323  -0.001190   0.001219  -0.000123   
technical_34    0.009525   0.007728   0.014672  -0.005734   0.000935   
technical_35    0.023139  -0.135584   0.002621   0.006412  -0.037172   
technical_36    0.027121  -0.053343   0.000359   0.007009  -0.026161   
technical_37   -0.018761   0.025998   0.001798   0.003780  -0.005348   
technical_38   -0.009708   0.032365  -0.003263   0.000685  -0.002898   
technical_39   -0.007421   0.029276  -0.002187   0.000230  -0.

In [4]:
a = twoSigmaDf.corr()

In [5]:
sampleDf = twoSigmaDf.sample(n=100000)

In [6]:
analyze.dist_analyze(twoSigmaDf, 'timestamp')

/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/bokeh/core/compat/bokeh_renderer.py:262: UserWarning: Path marker shapes currently not handled, defaulting to Circle
  warnings.warn("Path marker shapes currently not handled, defaulting to Circle")
/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/matplotlib/artist.py:224: MatplotlibDeprecationWarning: get_axes has been deprecated in mpl 1.5, please use the
axes property.  A removal date has not been set.
  stacklevel=1)
/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/bokeh/core/compat/bokeh_renderer.py:295: UserWarning: Path marker sizes support is limited and may not display as expected
  warnings.warn("Path marker sizes support is limited and may not display as expected")


In [ ]:
analyze.dist_analyze(twoSigmaDf, 'y')

In [7]:
neg_model = twoSigmaDf[twoSigmaDf.y< -0.08]
pos_model = twoSigmaDf[twoSigmaDf.y> 0.09]
central_model = twoSigmaDf[twoSigmaDf.y> -0.08][twoSigmaDf.y < 0.09]

/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/ipykernel/__main__.py:3: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  app.launch_new_instance()


In [8]:
analyze.dist_analyze(neg_model)

/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/bokeh/core/compat/bokeh_renderer.py:262: UserWarning: Path marker shapes currently not handled, defaulting to Circle
  warnings.warn("Path marker shapes currently not handled, defaulting to Circle")
/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/matplotlib/artist.py:224: MatplotlibDeprecationWarning: get_axes has been deprecated in mpl 1.5, please use the
axes property.  A removal date has not been set.
  stacklevel=1)
/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/bokeh/core/compat/bokeh_renderer.py:295: UserWarning: Path marker sizes support is limited and may not display as expected
  warnings.warn("Path marker sizes support is limited and may not display as expected")


In [ ]:
analyze.dist_analyze(pos_model)

/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/bokeh/core/compat/bokeh_renderer.py:262: UserWarning: Path marker shapes currently not handled, defaulting to Circle
  warnings.warn("Path marker shapes currently not handled, defaulting to Circle")
/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/matplotlib/artist.py:224: MatplotlibDeprecationWarning: get_axes has been deprecated in mpl 1.5, please use the
axes property.  A removal date has not been set.
  stacklevel=1)
/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/bokeh/core/compat/bokeh_renderer.py:295: UserWarning: Path marker sizes support is limited and may not display as expected
  warnings.warn("Path marker sizes support is limited and may not display as expected")


In [ ]:
analyze.dist_analyze(central_model)

In [18]:
len(neg_model.columns)

111

In [19]:
neg_model.describe()

/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/numpy/lib/function_base.py:3834: RuntimeWarning: Invalid value encountered in percentile
  RuntimeWarning)


id     timestamp     derived_0     derived_1    derived_2  \
count  13321.000000  13321.000000  11607.000000  1.154600e+04  9734.000000   
mean    1090.470235   1013.438781    -20.230871  8.389715e+11    -0.290759   
std      626.108964    630.249488    530.713684  6.374285e+13   106.757179   
min        0.000000      0.000000 -20174.919922 -6.978757e-02 -9848.299805   
25%      551.000000    321.000000           NaN           NaN          NaN   
50%     1113.000000   1392.000000           NaN           NaN          NaN   
75%     1638.000000   1573.000000           NaN           NaN          NaN   
max     2156.000000   1812.000000   3252.059326  4.861011e+15  3547.982422   

          derived_3     derived_4  fundamental_0  fundamental_1  \
count  10598.000000   9298.000000   12824.000000    5129.000000   
mean      -0.481507     62.374760       0.015859      -0.442700   
std       38.710842   1956.082275       0.274834       6.026238   
min    -3731.227051  -8551.914062      -2.262117    -105.965508   
25%             NaN           NaN            NaN            NaN   
50%             NaN           NaN            NaN            NaN   
75%             NaN           NaN            NaN            NaN   
max      402.463562  67859.648438       1.374609     111.245499   

       fundamental_2      ...       technical_36  technical_37  technical_38  \
count   10467.000000      ...       13301.000000  12892.000000  12892.000000   
mean       -0.863908      ...          -0.559916     -0.059979     -0.032170   
std        12.871026      ...           0.775995      0.216400      0.155373   
min      -845.541748      ...          -1.687572     -1.000000     -1.000000   
25%              NaN      ...                NaN           NaN           NaN   
50%              NaN      ...                NaN           NaN           NaN   
75%              NaN      ...                NaN           NaN           NaN   
max        76.771248      ...           7.150674     -0.000000     -0.000000   

       technical_39  technical_40  technical_41  technical_42  technical_43  \
count  12889.000000  13302.000000  12652.000000  12889.000000  13251.000000   
mean      -0.033868      0.306542      0.006144      0.013524     -1.485620   
std        0.161837      0.435849      0.112883      0.225721      0.840541   
min       -1.000000     -0.511626     -0.390842     -1.000000     -2.000000   
25%             NaN           NaN           NaN           NaN           NaN   
50%             NaN           NaN           NaN           NaN           NaN   
75%             NaN           NaN           NaN           NaN           NaN   
max       -0.000000      1.569265      0.523121      1.000000      0.000000   

       technical_44             y  
count  10662.000000  13321.000000  
mean       0.001547     -0.085585  
std        0.029322      0.001362  
min       -0.107395     -0.086094  
25%             NaN     -0.086094  
50%             NaN     -0.086094  
75%             NaN     -0.086094  
max        0.108497     -0.080002  

[8 rows x 111 columns]

In [20]:
pos_model.describe()

/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/numpy/lib/function_base.py:3834: RuntimeWarning: Invalid value encountered in percentile
  RuntimeWarning)


id     timestamp     derived_0     derived_1    derived_2  \
count  12325.000000  12325.000000  10795.000000  1.076700e+04  9151.000000   
mean    1099.071968   1030.205274    -20.194635  9.279557e+11     1.012873   
std      625.824963    631.370385    543.347778  5.961956e+13    49.709621   
min        0.000000      0.000000 -20174.945312 -6.899215e-02  -159.623215   
25%      565.000000    334.000000           NaN           NaN          NaN   
50%     1124.000000   1402.000000           NaN           NaN          NaN   
75%     1646.000000   1589.000000           NaN           NaN          NaN   
max     2158.000000   1812.000000   3252.521484  4.861364e+15  3434.219971   

          derived_3     derived_4  fundamental_0  fundamental_1  \
count   9817.000000   8706.000000   11947.000000   4.434000e+03   
mean      -4.101458     75.046547       0.023291  -2.353939e+09   
std      273.789276   1989.184448       0.278795   1.567448e+11   
min   -26025.376953  -6580.262695      -0.470179  -1.043737e+13   
25%             NaN           NaN            NaN            NaN   
50%             NaN           NaN            NaN            NaN   
75%             NaN           NaN            NaN            NaN   
max      646.564209  67859.570312       1.376526   1.112619e+02   

       fundamental_2      ...       technical_36  technical_37  technical_38  \
count    9839.000000      ...       12310.000000  12014.000000  12014.000000   
mean       -0.800734      ...          -0.641467     -0.052561     -0.031572   
std        17.587000      ...           0.731850      0.203786      0.156493   
min     -1010.358887      ...          -1.687572     -1.000000     -1.000000   
25%              NaN      ...                NaN           NaN           NaN   
50%              NaN      ...                NaN           NaN           NaN   
75%              NaN      ...                NaN           NaN           NaN   
max        76.771248      ...           6.613261     -0.000000     -0.000000   

       technical_39  technical_40  technical_41  technical_42  technical_43  \
count  12011.000000  12317.000000  11797.000000  12011.000000  12261.000000   
mean      -0.035106      0.345368      0.006302      0.016017     -1.534512   
std        0.167232      0.437216      0.112917      0.237751      0.813359   
min       -1.000000     -0.511626     -0.405803     -1.000000     -2.000000   
25%             NaN           NaN           NaN           NaN           NaN   
50%             NaN           NaN           NaN           NaN           NaN   
75%             NaN           NaN           NaN           NaN           NaN   
max       -0.000000      1.569265      0.531148      1.000000      0.000000   

       technical_44             y  
count   9897.000000  12325.000000  
mean       0.001739      0.093346  
std        0.029062      0.000580  
min       -0.119254      0.090013  
25%             NaN      0.093498  
50%             NaN      0.093498  
75%             NaN      0.093498  
max        0.100609      0.093498  

[8 rows x 111 columns]

In [21]:
central_model.describe()

/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/numpy/lib/function_base.py:3834: RuntimeWarning: Invalid value encountered in percentile
  RuntimeWarning)


id     timestamp     derived_0     derived_1     derived_2  \
count  1.685110e+06  1.685110e+06  1.615395e+06  1.607414e+06  1.293220e+06   
mean   1.093847e+03  9.444710e+02 -4.320179e+00  7.714311e+11 -3.419580e-01   
std    6.309304e+02  5.176048e+02  2.434235e+02  7.638954e+13  6.489404e+01   
min    0.000000e+00  0.000000e+00 -2.017497e+04 -7.375435e-02 -9.848880e+03   
25%    5.500000e+02  5.070000e+02           NaN           NaN           NaN   
50%    1.098000e+03  9.540000e+02           NaN           NaN           NaN   
75%    1.657000e+03  1.394000e+03           NaN           NaN           NaN   
max    2.158000e+03  1.812000e+03  3.252527e+03  1.068448e+16  3.823001e+03   

          derived_3     derived_4  fundamental_0  fundamental_1  \
count  1.540870e+06  1.286294e+06   1.662038e+06   1.022123e+06   
mean  -4.819597e-01  1.732592e+01  -2.100542e-02  -5.655002e+08   
std    1.003563e+02  9.027844e+02   2.491874e-01   7.466475e+10   
min   -3.434176e+04 -8.551914e+03  -2.344957e+00  -1.043737e+13   
25%             NaN           NaN            NaN            NaN   
50%             NaN           NaN            NaN            NaN   
75%             NaN           NaN            NaN            NaN   
max    1.239737e+03  6.785965e+04   1.378195e+00   5.203165e+02   

       fundamental_2      ...       technical_36  technical_37  technical_38  \
count   1.321610e+06      ...       1.682593e+06  1.666685e+06  1.666685e+06   
mean   -1.520521e-01      ...      -7.803028e-02 -9.160292e-02 -8.235334e-02   
std     3.177889e+00      ...       6.071518e-01  2.481735e-01  2.342655e-01   
min    -1.077101e+03      ...      -1.687572e+00 -1.000000e+00 -1.000000e+00   
25%              NaN      ...                NaN           NaN           NaN   
50%              NaN      ...                NaN           NaN           NaN   
75%              NaN      ...                NaN           NaN           NaN   
max     7.677125e+01      ...       4.957758e+01  0.000000e+00  0.000000e+00   

       technical_39  technical_40  technical_41  technical_42  technical_43  \
count  1.665840e+06  1.682901e+06  1.642118e+06  1.665855e+06  1.680558e+06   
mean  -7.347512e-02  4.487170e-02  5.221669e-03 -1.747572e-02 -9.654344e-01   
std    2.237579e-01  3.062875e-01  1.134475e-01  2.117927e-01  9.622647e-01   
min   -1.000000e+00 -5.250904e-01 -4.449529e-01 -1.000000e+00 -2.000000e+00   
25%             NaN           NaN           NaN           NaN           NaN   
50%             NaN           NaN           NaN           NaN           NaN   
75%             NaN           NaN           NaN           NaN           NaN   
max    0.000000e+00  1.569265e+00  6.844833e-01  1.000000e+00  0.000000e+00   

       technical_44             y  
count  1.453418e+06  1.685110e+06  
mean   3.704605e-04  2.189479e-04  
std    3.014728e-02  1.971635e-02  
min   -1.265686e-01 -7.999922e-02  
25%             NaN -9.355492e-03  
50%             NaN -1.468537e-04  
75%             NaN  9.340377e-03  
max    1.435858e-01  8.999928e-02  

[8 rows x 111 columns]

In [22]:
central_model.corr()

id  timestamp  derived_0  derived_1  derived_2  \
id              1.000000   0.003379   0.025829   0.006673  -0.003213   
timestamp       0.003379   1.000000   0.020692   0.006903   0.004907   
derived_0       0.025829   0.020692   1.000000   0.000158   0.000208   
derived_1       0.006673   0.006903   0.000158   1.000000   0.000064   
derived_2      -0.003213   0.004907   0.000208   0.000064   1.000000   
derived_3      -0.005844   0.004479  -0.000076   0.000030  -0.000029   
derived_4      -0.027889  -0.022004  -0.964022  -0.000196  -0.000136   
fundamental_0  -0.034017  -0.054091   0.013089  -0.009310  -0.001375   
fundamental_1  -0.010688   0.006272   0.000295   0.000058  -0.000189   
fundamental_2   0.017667   0.030277   0.011640   0.000028   0.000601   
fundamental_3  -0.069848   0.045901  -0.001819  -0.005298   0.005564   
fundamental_5   0.007698   0.012447  -0.000102  -0.000423   0.000268   
fundamental_6   0.013073   0.046469   0.000136   0.000917   0.000892   
fundamental_7  -0.010523  -0.017054   0.000121  -0.000106   0.001468   
fundamental_8   0.004138   0.074585   0.002810  -0.002162   0.000565   
fundamental_9   0.005828  -0.008614  -0.031385   0.001500   0.012011   
fundamental_10 -0.004541   0.030283  -0.000066  -0.000233   0.000655   
fundamental_11  0.009892   0.043685   0.023386   0.000223   0.000683   
fundamental_12 -0.006486   0.020769   0.000269  -0.000251   0.000300   
fundamental_13  0.001083   0.005335  -0.000648  -0.001627  -0.000082   
fundamental_14  0.002856   0.000335   0.000826  -0.000102  -0.000019   
fundamental_15  0.006335   0.030577  -0.003001  -0.000469   0.000840   
fundamental_16 -0.005718  -0.007611   0.001261   0.000402   0.000134   
fundamental_17 -0.011063  -0.014180   0.000158  -0.000091   0.000077   
fundamental_18 -0.013455  -0.035178   0.006374  -0.000268   0.000351   
fundamental_19  0.010876  -0.002604  -0.000273  -0.000317   0.001628   
fundamental_20  0.008333   0.015831  -0.000072   0.000060  -0.000124   
fundamental_21 -0.010920  -0.143165  -0.013051   0.000377  -0.000496   
fundamental_22  0.010628   0.001429   0.002828  -0.000746   0.000915   
fundamental_23 -0.023809  -0.019134  -0.000226  -0.000247   0.000058   
...                  ...        ...        ...        ...        ...   
technical_13   -0.003370  -0.005462   0.002600  -0.000847   0.000596   
technical_14    0.017544  -0.080030   0.011007  -0.006614  -0.003020   
technical_16    0.000834   0.036496   0.002887  -0.005629   0.000755   
technical_17    0.006801   0.000367   0.006468   0.005400  -0.004957   
technical_18   -0.019320   0.035921  -0.003550   0.002160   0.001230   
technical_19    0.002243   0.002323  -0.002829   0.005739   0.003155   
technical_20    0.008869   0.023440  -0.012950   0.003171   0.004647   
technical_21    0.006070   0.004939   0.003708   0.001877   0.000148   
technical_22    0.008344   0.001998  -0.023962   0.004637  -0.002864   
technical_24   -0.002196  -0.000657  -0.000260  -0.002408  -0.017027   
technical_25   -0.005317  -0.000650   0.000461   0.000565   0.004780   
technical_27    0.015070  -0.009978  -0.004978   0.001147  -0.010237   
technical_28   -0.006005   0.002068   0.012755  -0.007884   0.006147   
technical_29    0.028993  -0.173718   0.018226  -0.000808  -0.003726   
technical_30    0.000684   0.015651  -0.008464  -0.002594  -0.002096   
technical_31    0.001133  -0.006388  -0.009834  -0.001185   0.001376   
technical_32   -0.022933   0.002942  -0.000995  -0.007059  -0.001400   
technical_33   -0.006499   0.003146  -0.001398   0.001200   0.000038   
technical_34    0.008832   0.011046   0.014229  -0.005942   0.001190   
technical_35    0.023486  -0.137176   0.002412   0.006522  -0.037393   
technical_36    0.027866  -0.052895   0.000237   0.007151  -0.027177   
technical_37   -0.018918   0.027044   0.001783   0.003776  -0.004997   
technical_38   -0.009763   0.032154  -0.003323   0.000866  -0.002713   
technical_39   -0.007357   0.029084  -0.002217   0.000415  -0.

In [ ]:
prediction = 2.217474e-04
mean = twoSigmaDf['y'].mean()
sampleDf['rmse_pred'] = sampleDf['y'].apply(lambda x: (x-prediction)**2)
sampleDf['rmse_mean'] = sampleDf['y'].apply(lambda x: (x-mean)**2)

r_square = 1 - sampleDf['rmse_pred'].sum()/sampleDf['rmse_mean'].sum()

In [ ]:
out = np.sqrt(abs(r_square))
print(out* -1)

In [24]:
sample2Df = twoSigmaDf.sample(n=300000)
prediction = 2.217474e-04
mean = sample2Df['y'].mean()
sample2Df['rmse_pred'] = sample2Df['y'].apply(lambda x: (x-prediction)**2)
sample2Df['rmse_mean'] = sample2Df['y'].apply(lambda x: (x-mean)**2)

r_square = 1 - sample2Df['rmse_pred'].sum()/sample2Df['rmse_mean'].sum()
out = np.sqrt(abs(r_square))
print(out, r_square)


0.00100146381856 -1.00292977989e-06


In [25]:
sample6Df = twoSigmaDf.sample(n=600000)
prediction = 0
mean = sample6Df['y'].mean()
sample6Df['rmse_pred'] = sample6Df['y'].apply(lambda x: (x-prediction)**2)
sample6Df['rmse_mean'] = sample6Df['y'].apply(lambda x: (x-mean)**2)

r_square = 1 - sample6Df['rmse_pred'].sum()/sample6Df['rmse_mean'].sum()
out = np.sqrt(abs(r_square))
print(out, r_square)

0.0098337868428 -9.67033636696e-05


In [26]:
prediction = 0
mean = twoSigmaDf['y'].mean()
central_mean = central_model['y'].mean()
def get_prediction(x):
    if x <= -0.08:
        return -0.085
    elif x >= 0.09:
        return 0.095
    else:
        return central_mean

def get_r_square(prediction, actual):
    assert len(prediction) == len(actual), "Lengths of actuals and predictions should be equal"
    rmse_pred = 0
    rmse_mean = 0
    mean = np.mean(actual)
    for pred,ea in zip(prediction, actual):
        rmse_pred += (ea - pred)**2
        rmse_mean += (ea - mean)**2
    return 1 - rmse_pred/rmse_mean
    
    
    pass
    
#twoSigmaDf['prediction'] = twoSigmaDf['y'].apply(lambda x: get_prediction(x))
twoSigmaDf['rmse_pred'] = twoSigmaDf['y'].apply(lambda x: (x-get_prediction(x))**2)
twoSigmaDf['rmse_mean'] = twoSigmaDf['y'].apply(lambda x: (x-mean)**2)

r_square = 1 - twoSigmaDf['rmse_pred'].sum()/twoSigmaDf['rmse_mean'].sum()
out = np.sqrt(abs(r_square))

print(out, r_square)
print(get_r_square(twoSigmaDf['y'].apply(lambda x: get_prediction(x)), twoSigmaDf['y']))

0.488130830732 0.238271707911
0.238271710002


In [27]:
def get_category(x):
    if x <= -0.08:
        return 'Neg'
    elif x >= 0.09:
        return "Pos"
    else:
        return "Mid"
twoSigmaDf['category'] = twoSigmaDf['y'].apply(lambda x: get_category(x))


In [28]:
a = twoSigmaDf.groupby('category').describe()

/home/anand/anaconda3/envs/analytics/lib/python3.5/site-packages/numpy/lib/function_base.py:3834: RuntimeWarning: Invalid value encountered in percentile
  RuntimeWarning)


In [29]:
b = a.transpose().reset_index()
b.columns

MultiIndex(levels=[['Mid', 'Neg', 'Pos', 'index'], ['count', 'mean', 'std', 'min', '25%', '50%', '75%', 'max', '']],
           labels=[[3, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2, 2, 2, 2, 2], [8, 0, 1, 2, 3, 4, 5, 6, 7, 0, 1, 2, 3, 4, 5, 6, 7, 0, 1, 2, 3, 4, 5, 6, 7]],
           names=['category', None])

In [30]:
from datascienceutils import utils
anova_dict = dict()
for col in twoSigmaDf.columns:
    anova_dict[col] = utils.calculate_anova(sample2Df, 'y', col)
print(anova_dict)

MemoryError: 

In [ ]:
filteredDf = twoSigmaDf[['id', 'timestamp', 'technical_34', 'technical_20']]
filteredDf.fillna(filteredDf.mean(), inplace=True)
target = twoSigmaDf['category']
from sklearn.naive_bayes import GaussianNB
gnb = GaussianNB()
#gnb_model = pm.train(filteredDf, target, 'gaussianNB')
gnb.fit(filteredDf, target)



In [ ]:
def get_pred_by_category(x):
    if x == 'Mid':
        return 0
    elif x == 'Neg':
        return -0.085
    else:
        return 0.095
num_predictions = list(map(get_pred_by_category, gnb.predict(filteredDf)))

get_r_square(num_predictions, list(twoSigmaDf['y']))